## Pytesseract attempt

In [47]:
%pip install opencv-python
%pip install matplotlib
%pip install pytesseract
%pip install regex
%pip install scipy

Note: you may need to restart the kernel to use updated packages.


You should consider upgrading via the 'c:\Users\Lim Hui Xuan\Desktop\coding\work\ocr\tessenv\Scripts\python.exe -m pip install --upgrade pip' command.


Note: you may need to restart the kernel to use updated packages.


You should consider upgrading via the 'c:\Users\Lim Hui Xuan\Desktop\coding\work\ocr\tessenv\Scripts\python.exe -m pip install --upgrade pip' command.


Note: you may need to restart the kernel to use updated packages.


You should consider upgrading via the 'c:\Users\Lim Hui Xuan\Desktop\coding\work\ocr\tessenv\Scripts\python.exe -m pip install --upgrade pip' command.


Note: you may need to restart the kernel to use updated packages.


You should consider upgrading via the 'c:\Users\Lim Hui Xuan\Desktop\coding\work\ocr\tessenv\Scripts\python.exe -m pip install --upgrade pip' command.


Note: you may need to restart the kernel to use updated packages.


You should consider upgrading via the 'c:\Users\Lim Hui Xuan\Desktop\coding\work\ocr\tessenv\Scripts\python.exe -m pip install --upgrade pip' command.


In [4]:
import cv2
import pytesseract
import os
from PIL import Image
from matplotlib import pyplot as plt
import numpy as np
import imutils

In [24]:
def biggest_contour(contours):
    biggest = np.array([])
    max_area = 0
    for i in contours:
        area = cv2.contourArea(i)
        if area > 1000:
            peri = cv2.arcLength(i, True)
            approx = cv2.approxPolyDP(i, 0.15 * peri, True)
            print(approx)
            if area > max_area and len(approx) >= 4:
                biggest = approx
                max_area = area
    return biggest

def correct_skew(image):
    img = image.copy()
    
    #greyscale and search for edges
    #grayscale = cv2.cvtColor(img, cv2.COLOR_RGB2GRAY)
    grayscale = cv2.bilateralFilter(img, 20, 30, 30)
    edged = cv2.Canny(grayscale, 230, 240)
    
    #grayscale = np.stack((grayscale,) * 3, axis = -1)
    #edged = np.stack((edged,) * 3, axis = -1)
    #img_hor = np.hstack((img, grayscale, edged))
    
    # contour detection
    contours, hierachy = cv2.findContours(grayscale.copy(), cv2.RETR_TREE, cv2.CHAIN_APPROX_SIMPLE)
    print(contours)
    contours = sorted(contours, key = cv2.contourArea, reverse = True)[:1] # largest contour area
    biggest = biggest_contour(contours)
    
    # testing
    cv2.drawContours(img, [biggest], -1, (0, 255, 0), 3)
    
    # pixel values of the contours in the image
    points = biggest.reshape(4, 2)
    input_points = np.zeros((4, 2), dtype = "float32")
    
    points_sum = points.sum(axis = 1)
    input_points[0] = points[np.argmin(points_sum)]
    input_points[3] = points[np.argmax(points_sum)]
    
    points_diff = np.diff(points, axis = 1)
    input_points[1] = points[np.argmin(points_diff)]
    input_points[2] = points[np.argmax(points_diff)]
    
    (top_left, top_right, bottom_right, bottom_left) = input_points
    bottom_width = np.sqrt(((bottom_right[0] - bottom_left[0]) ** 2) + (bottom_right[1] - bottom_left[1]) ** 2)
    top_width =  np.sqrt(((top_right[0] - top_left[0]) ** 2) + (top_right[1] - top_left[1]) ** 2)
    right_height =  np.sqrt(((top_right[0] - bottom_right[0]) ** 2) + (top_right[1] - bottom_right[1]) ** 2)
    left_height =  np.sqrt(((top_left[0] - bottom_left[0]) ** 2) + (top_left[1] - bottom_left[1]) ** 2)
    
    #output image size
    max_width = max(int(bottom_width), int(top_width))
    max_height = max(int(right_height), int(left_height))
    
    #desired points
    converted_points = np.float32([[0, 0], [max_width, 0], [0, max_height], [max_width, max_height]])
    
    # perform the perspective transformation
    matrix = cv2.getPerspectiveTransform(input_points, converted_points)
    img_output = cv2.warpPerspective(img, matrix, (max_width, max_height))
    
    return img_output
    

In [ ]:
def correct_skew(image):
    img = image.copy()
    
    #greyscale and search for edges
    #grayscale = cv2.cvtColor(img, cv2.COLOR_RGB2GRAY)
    grayscale = cv2.bilateralFilter(img, 20, 30, 30)
    edged = cv2.Canny(grayscale, 230, 240)
    
    # contour detection
    cnts = contours[0]
    screenCnt = 0

    for contour in contours:
        # get rectangle bounding contour
        [x,y,w,h] = cv2.boundingRect(contour)

    # draw rectangle around contour on original image
    #cv2.rectangle(image,(x,y),(x+w,y+h),(255,0,255),2)

    ##### code added..for thresholding
    for c in cnts:
        # approximate the contour
        peri = cv2.arcLength(c, True)
        approx = cv2.approxPolyDP(c, 0.02 * peri, True)

        # if our approximated contour has four points, then
        # we can assume that we have found our screen
        if len(approx) == 4:
            screenCnt = approx
            break

    # show the contour (outline) of the piece of paper
    print("STEP 2: Find contours of paper")
    cv2.drawContours(image, [screenCnt], -1, (0, 255, 0), 2)
    
    #TODO: find the variables required
    matrix = cv2.getPerspectiveTransform(input_points, converted_points)
    img_output = cv2.warpPerspective(img, matrix, (max_width, max_height))
    
    

In [25]:
def preprocess_img(img):
    #color to greyscale
    grayscale = cv2.cvtColor(img, cv2.COLOR_BGR2GRAY)
    
    #normalize image
    norm_img = np.zeros((img.shape[0], img.shape[1]))
    norm = cv2.normalize(grayscale, norm_img, 0, 255, cv2.NORM_MINMAX)
    blur = cv2.medianBlur(norm, 5)
    canny = cv2.Canny(blur, 40, 50)
    
    # denoise the image
    #img = cv2.fastNlMeansDenoisingColored(norm, None, 10, 10, 7, 15)
    
    #thresh = cv2.threshold(grayscale, 0, 255, cv2.THRESH_BINARY | cv2.THRESH_OTSU)[1]
    #dist = cv2.distanceTransform(thresh, cv2.DIST_L2, 5)
    #dist = cv2.normalize(dist, dist, 0, 1.0, cv2.NORM_MINMAX)
    #dist = (dist * 255).astype("uint8")

    return canny

In [26]:
test_path = "./test/096.jpg_Canon.jpg"
proc_img = preprocess_img(cv2.imread(test_path))
correct_skew(proc_img)

cv2.namedWindow('result', cv2.WINDOW_NORMAL)
cv2.imshow("result", proc_img)
cv2.waitKey(0)

print(pytesseract.image_to_string(proc_img))
#print(pytesseract.image_to_string(Image.open(test_path)))

(array([[[3289, 2675]],

       [[3290, 2676]],

       [[3292, 2676]],

       [[3293, 2677]],

       [[3295, 2677]],

       [[3293, 2677]],

       [[3292, 2676]],

       [[3290, 2676]]], dtype=int32), array([[[3508, 2546]],

       [[3509, 2546]],

       [[3510, 2547]],

       [[3512, 2547]],

       [[3510, 2547]],

       [[3509, 2546]]], dtype=int32), array([[[3482, 2504]],

       [[3484, 2506]],

       [[3485, 2506]],

       [[3487, 2508]],

       [[3488, 2508]],

       [[3487, 2507]],

       [[3486, 2507]],

       [[3483, 2504]]], dtype=int32), array([[[3399, 2480]],

       [[3400, 2480]],

       [[3401, 2481]],

       [[3405, 2481]],

       [[3407, 2483]],

       [[3405, 2481]],

       [[3403, 2481]],

       [[3402, 2480]],

       [[3401, 2481]],

       [[3400, 2480]]], dtype=int32), array([[[3406, 2477]],

       [[3411, 2477]],

       [[3412, 2478]],

       [[3414, 2478]],

       [[3412, 2478]],

       [[3411, 2477]]], dtype=int32), array([[[3254, 24

error: OpenCV(4.7.0) D:\a\opencv-python\opencv-python\opencv\modules\imgproc\src\drawing.cpp:2605: error: (-215:Assertion failed) reader.ptr != NULL in function 'cvDrawContours'


In [1]:
import regex as re

def extract_text(img_path, lang):
    return pytesseract.image_to_string(Image.open(img_path), lang = lang)

def extract_name(ocr_result):
    # Define pattern to extract company
    company_pattern = r'(?i)(?:^|\b)([A-Z][A-Za-z]+(?: [A-Z][A-Za-z]+)*)(?:\b|$)'

    # Extract company using regular expression pattern
    company_match = re.search(company_pattern, ocr_result)
    if company_match:
        return company_match.group(1)
    else:
        return None

def extract_email(ocr_result):
    # Extract email address using regular expression pattern
    email_pattern = r'\b[A-Za-z0-9._%+-]+@[A-Za-z0-9.-]+\.[A-Z|a-z]{2,}\b'
    email_match = re.search(email_pattern, ocr_result, re.I)
    if email_match:
        return email_match.group()
    else:
        return None

def extract_company(ocr_result):
    # TODO: Define pattern to extract company
    company_pattern = r'(?i)(?:^|\b)([A-Z][A-Za-z]+(?: [A-Z][A-Za-z]+)*)(?:\b|$)'

    # Extract company using regular expression pattern
    company_match = re.search(company_pattern, ocr_result)
    if company_match:
        return company_match.group(1)
    else:
        return None

def extract_contact(ocr_result):
    # Extract contact number using regular expression pattern
    contact_number_pattern = r'\b\d+\b'
    contact_number_matches = re.findall(contact_number_pattern, ocr_result)
    contact_number = ''.join(contact_number_matches)
    if contact_number:
        return contact_number
    else:
        return None

In [25]:
# extract functions
extract_company(extract_text(test_path, lang = "eng"))

'Ale iS Beckman'

In [17]:
extract_name(extract_text(test_path, lang = "eng"))

'Alexis Beckman'

In [18]:
extract_email(extract_text(test_path, lang = "eng"))

'info@culturefrozenyogurt.com'

In [19]:
extract_contact(extract_text(test_path, lang = "eng"))

'6503240440650324044834094306100'

In [20]:
import json

# function to produce the json
def extract_json(img_path, lang):
    res_dict = {}
    
    extracted_txt = extract_text(img_path, lang = lang)
    res_dict["name"], res_dict["email"], res_dict["contact"], res_dict["company"] = extract_name(extracted_txt), extract_email(extracted_txt), extract_contact(extracted_txt), extract_contact(extracted_txt)
    
    res_json = json.dumps(res_dict)
    return res_json
    

In [21]:
# testing the json function
extract_json(test_path, "eng")

'{"name": "Alexis Beckman", "email": "info@culturefrozenyogurt.com", "contact": "6503240440650324044834094306100", "company": "6503240440650324044834094306100"}'